In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, lit, when
from pyspark.sql.types import StructType,ArrayType,StructField,StringType
from snowflake.snowpark import Session

In [0]:
region_a_path = '/FileStore/tables/order_region_a.xlsx'
region_b_path = '/FileStore/tables/order_region_b.xlsx'


In [0]:
def flatten_struct(schema):
    def wrapper(schema,prefix = ""):
        flatten_cols = []        
        for field in schema.fields:
            path = f'{prefix}.{field.name}' if prefix  else f'{field.name}'
            if isinstance(field.dataType,StructType):
                  flatten_cols+=wrapper(field.dataType,path)
            else:
                  flatten_cols.append(path)
        return flatten_cols
    
    return [col(cols).alias(cols.replace('.','_')) for cols in wrapper(schema)]  


In [0]:
from pyspark.sql.functions import from_json, col

def flatten_drop(df):
  schema = StructType([
      StructField("CurrencyCode", StringType(), True),
      StructField("Amount", StringType(), True)
  ])
  parsed_df = df.withColumn("PromotionDiscount", from_json(col("PromotionDiscount"), schema))
  return parsed_df.select(flatten_struct(parsed_df.schema)).drop('PromotionDiscount')

In [0]:
def create_spark_session():
    # Create a SparkSession
    return SparkSession.builder.appName("sales_etl") \
                .config("spark.jars.packages", "com.crealytics:spark-excel-2.12.17-3.2.2_2.12:3.2.2_0.18.1") \
                .getOrCreate()

def read_files(spark):
    # Read Region A data
    df_region_a = spark.read \
        .format("com.crealytics.spark.excel") \
        .option("header", "true") \
        .option("inferSchema", "true") \
        .load(region_a_path)

    df_region_a  = flatten_drop(df_region_a.withColumn('region',lit('A')))

    # Read Region A data
    df_region_b = spark.read \
        .format("com.crealytics.spark.excel") \
        .option("header", "true") \
        .option("inferSchema", "true") \
        .load(region_b_path)

    df_region_b  = flatten_drop(df_region_b.withColumn('region',lit('B')))

    return (df_region_a,df_region_b)

def transform_data(df_region_a, df_region_b):
    # Combine datasets
    combined_df = df_region_a.union(df_region_b)
    
    # Add required columns and apply transformations
    transformed_df = combined_df \
        .withColumn("total_sales", col("QuantityOrdered") * col("ItemPrice")) \
        .withColumn("net_sale", col("total_sales") - col("PromotionDiscount_Amount")) \
        .dropDuplicates(["OrderId","region"]).where(col("net_sale") > 0)
        
    return transformed_df

def create_snowflake_connection(snowflake_configs):
    # Establish connection to Snowflake
    return Session.builder.configs(snowflake_configs).create()

def upload_to_snowflake(df,session, table_name):
    # Convert DataFrame to Pandas DataFrame
    pandas_df = df.toPandas()
    
    # Create table and upload data
    pandas_df.to_sql(
        name=table_name,
        con=session.connection,
        if_exists='replace',
        index=False
    )

def load_to_sf(df):
    # save as temp table
    df.createOrReplaceTempView("sales_data")  




In [0]:
# # create spark session
spark = create_spark_session()

# # Extract
df_region_a, df_region_b = read_files(spark)

# # Transform
transformed_df = transform_data(df_region_a, df_region_b)

# # Load
load_to_sf(transformed_df)

In [0]:
display(df_region_a)

OrderId OrderItemId QuantityOrdered ItemPrice PromotionDiscount_CurrencyCode PromotionDiscount_Amount batch_id region 171-0001135-1657958 1.1168926687715E13 1.0 949.0 INR 10 359.0 A 171-0001497-9165123 1.9760298917699E13 1.0 699.0 INR 10.1 1135.0 A 171-0002127-1363507 5.949764099083E12 1.0 399.0 INR 10 297.0 A 171-0002370-0601169 5.7571868836379E13 1.0 499.0 INR 10.1 114.0 A 171-0004526-2028348 3.3851287891403E13 1.0 1699.0 INR 10 764.0 A 171-0004781-3853173 4.3686103544491E13 1.0 399.0 INR 10.1 809.0 A 171-0004947-4305927 1.5941372058555E13 1.0 1399.0 INR 10 15.0 A 171-0004947-4305927 1.5941372058555E13 1.0 1399.0 INR 10.1 330.0 A 171-0005467-8036365 3.3952397753619E13 1.0 349.0 INR 10 868.0 A 171-0006030-2254725 3.1456208605443E13 1.0 499.0 INR 10.1 1494.0 A 171-0006682-9937168 2.915892310475E12 1.0 549.0 INR 10 255.0 A 171-0008037-3788355 2.2456900251507E13 1.0 499.0 INR 10.1 232.0 A 171-0008659-1412343 4.5841722968955E13 1.0 2899.0 INR 10 184.0 A 171-0008662-0057942 6.6326653881907E13 1.0 599.0 INR 10.1 122.0 A 171-0010322-1769977 4.7459215833307E13 1.0 399.0 INR 10 676.0 A 171-0010803-5365973 2.1135179938611E13 1.0 299.0 INR 10.1 669.0 A 171-0011025-3910737 1.8207721515083E13 1.0 1499.0 INR 10 821.0 A 171-0015661-5525128 5.2322576555467E13 1.0 1199.0 INR 10.1 31.0 A 171-0015668-5065935 8.918074736283E12 1.0 699.0 INR 10 709.0 A 171-0016430-9547521 3.526651130627E12 1.0 499.0 INR 10.1 325.0 A 171-0016468-7483547 4.1088062877059E13 1.0 369.0 INR 10 529.0 A 171-0016656-1255573 2.1577356095867E13 1.0 499.0 INR 10.1 695.0 A 171-0017311-5318712 6.4258514309019E13 1.0 699.0 INR 10 577.0 A 171-0018170-2421930 3.1602125314219E13 1.0 799.0 INR 10.1 800.0 A 171-0018345-8874731 5.9365948515931E13 1.0 599.0 INR 10 150.0 A 171-0018448-9529112 2.4636780135115E13 1.0 299.0 INR 10.1 1576.0 A 171-0020330-4809129 4.7116361074315E13 1.0 849.0 INR 10 975.0 A 171-0020871-3057976 3.1639315030563E13 1.0 1139.0 INR 10.1 296.0 A 171-0021483-3525174 6.4370725651027E13 1.0 1599.0 INR 10 911.0 A 171-0022424-6354758 2.5431618871923E13 1.0 949.0 INR 10.1 874.0 A 171-0022691-4700335 6.0239001823435E13 1.0 499.0 INR 10 64.0 A 171-0022807-7934716 5.924271021683E12 1.0 999.0 INR 10.1 1329.0 A 171-0023361-7532373 5.0005747130291E13 1.0 1999.0 INR 10 283.0 A 171-0023912-2838777 1.2927344177755E13 1.0 499.0 INR 10.1 910.0 A 171-0024838-4383551 2.8167659511651E13 1.0 629.0 INR 10 560.0 A 171-0025528-4025152 4.9285731071411E13 1.0 549.0 INR 10.1 872.0 A 171-0025941-8385108 4.3956719994907E13 1.0 699.0 INR 10 206.0 A 171-0026175-0529902 5.2856990732539E13 1.0 349.0 INR 10.1 356.0 A 171-0027025-7137139 3.3479083386379E13 1.0 2689.0 INR 10 19.0 A 171-0027025-7137139 3.3479083386379E13 1.0 2689.0 INR 10.1 223.0 A 171-0027360-2156323 1.8670951823891E13 1.0 399.0 INR 10 462.0 A 171-0027470-8653903 2.5200477199443E13 1.0 465.25 INR 10.1 461.0 A 171-0027915-8460372 1.9370589564219E13 1.0 499.0 INR 10 1477.0 A 171-0028127-6647532 5.1764575498947E13 1.0 699.0 INR 10.1 275.0 A 171-0028216-8371541 1.0924415207611E13 1.0 1749.0 INR 10 700.0 A 171-0028333-6781103 8.089608438643E12 1.0 499.0 INR 10.1 1581.0 A 171-0029459-4938769 1.2269526562963E13 1.0 549.0 INR 10 859.0 A 171-0029785-0689923 5.4884465800555E13 1.0 521.0 INR 10.1 652.0 A 171-0030933-1962721 5.7741977969195E13 1.0 499.0 INR 10 444.0 A 171-0030987-7733153 2.3573653923531E13 1.0 499.0 INR 10.1 546.0 A 171-0032103-6712352 2.9477890050147E13 1.0 749.0 INR 10 884.0 A 171-0033662-2427509 3.0127765315035E13 1.0 499.0 INR 10.1 707.0 A 171-0034191-0141945 4.823379397067E12 1.0 499.0 INR 10 1066.0 A 171-0034857-3794740 3.5860646838875E13 2.0 1198.0 INR 10.1 188.0 A 171-0035112-3975520 6.9707840339043E13 1.0 299.0 INR 10 289.0 A 171-0035681-2079506 1.6527618056675E13 1.0 799.0 INR 10.1 1320.0 A 171-0036328-6765939 4.6686953781939E13 1.0 499.0 INR 10 229.0 A 171-0036756-9277149 3.0626920791755E13 1.0 1699.0 INR 10.1 730.0 A 171-0036856-5109160 5.9029121588163E13 1.0 699.0 INR 10 1372.0 A 171-0037142-9207550 2.4699053937387

In [0]:
display(df_region_b)

OrderId OrderItemId QuantityOrdered ItemPrice PromotionDiscount_CurrencyCode PromotionDiscount_Amount batch_id region 171-0001135-1657958 1.1168926687715E13 1.0 949.0 INR 10 359.0 B 171-0001497-9165123 1.9760298917699E13 1.0 699.0 INR 10.1 1135.0 B 171-0002127-1363507 5.949764099083E12 1.0 399.0 INR 10 297.0 B 171-0002370-0601169 5.7571868836379E13 1.0 499.0 INR 10.1 114.0 B 171-0004526-2028348 3.3851287891403E13 1.0 1699.0 INR 10 764.0 B 171-0004781-3853173 4.3686103544491E13 1.0 399.0 INR 10.1 809.0 B 171-0004947-4305927 1.5941372058555E13 1.0 1399.0 INR 10 15.0 B 171-0004947-4305927 1.5941372058555E13 1.0 1399.0 INR 10.1 330.0 B 171-0005467-8036365 3.3952397753619E13 1.0 349.0 INR 10 868.0 B 171-0006030-2254725 3.1456208605443E13 1.0 499.0 INR 10.1 1494.0 B 171-0006682-9937168 2.915892310475E12 1.0 549.0 INR 10 255.0 B 171-0008037-3788355 2.2456900251507E13 1.0 499.0 INR 10.1 232.0 B 171-0008659-1412343 4.5841722968955E13 1.0 2899.0 INR 10 184.0 B 171-0008662-0057942 6.6326653881907E13 1.0 599.0 INR 10.1 122.0 B 171-0010322-1769977 4.7459215833307E13 1.0 399.0 INR 10 676.0 B 171-0010803-5365973 2.1135179938611E13 1.0 299.0 INR 10.1 669.0 B 171-0011025-3910737 1.8207721515083E13 1.0 1499.0 INR 10 821.0 B 171-0015661-5525128 5.2322576555467E13 1.0 1199.0 INR 10.1 31.0 B 171-0015668-5065935 8.918074736283E12 1.0 699.0 INR 10 709.0 B 171-0016430-9547521 3.526651130627E12 1.0 499.0 INR 10.1 325.0 B 171-0016468-7483547 4.1088062877059E13 1.0 369.0 INR 10 529.0 B 171-0016656-1255573 2.1577356095867E13 1.0 499.0 INR 10.1 695.0 B 171-0017311-5318712 6.4258514309019E13 1.0 699.0 INR 10 577.0 B 171-0018170-2421930 3.1602125314219E13 1.0 799.0 INR 10.1 800.0 B 171-0018345-8874731 5.9365948515931E13 1.0 599.0 INR 10 150.0 B 171-0018448-9529112 2.4636780135115E13 1.0 299.0 INR 10.1 1576.0 B 171-0020330-4809129 4.7116361074315E13 1.0 849.0 INR 10 975.0 B 171-0020871-3057976 3.1639315030563E13 1.0 1139.0 INR 10.1 296.0 B 171-0021483-3525174 6.4370725651027E13 1.0 1599.0 INR 10 911.0 B 171-0022424-6354758 2.5431618871923E13 1.0 949.0 INR 10.1 874.0 B 171-0022691-4700335 6.0239001823435E13 1.0 499.0 INR 10 64.0 B 171-0022807-7934716 5.924271021683E12 1.0 999.0 INR 10.1 1329.0 B 171-0023361-7532373 5.0005747130291E13 1.0 1999.0 INR 10 283.0 B 171-0023912-2838777 1.2927344177755E13 1.0 499.0 INR 10.1 910.0 B 171-0024838-4383551 2.8167659511651E13 1.0 629.0 INR 10 560.0 B 171-0025528-4025152 4.9285731071411E13 1.0 549.0 INR 10.1 872.0 B 171-0025941-8385108 4.3956719994907E13 1.0 699.0 INR 10 206.0 B 171-0026175-0529902 5.2856990732539E13 1.0 349.0 INR 10.1 356.0 B 171-0027025-7137139 3.3479083386379E13 1.0 2689.0 INR 10 19.0 B 171-0027025-7137139 3.3479083386379E13 1.0 2689.0 INR 10.1 223.0 B 171-0027360-2156323 1.8670951823891E13 1.0 399.0 INR 10 462.0 B 171-0027470-8653903 2.5200477199443E13 1.0 465.25 INR 10.1 461.0 B 171-0027915-8460372 1.9370589564219E13 1.0 499.0 INR 10 1477.0 B 171-0028127-6647532 5.1764575498947E13 1.0 699.0 INR 10.1 275.0 B 171-0028216-8371541 1.0924415207611E13 1.0 1749.0 INR 10 700.0 B 171-0028333-6781103 8.089608438643E12 1.0 499.0 INR 10.1 1581.0 B 171-0029459-4938769 1.2269526562963E13 1.0 549.0 INR 10 859.0 B 171-0029785-0689923 5.4884465800555E13 1.0 521.0 INR 10.1 652.0 B 171-0030933-1962721 5.7741977969195E13 1.0 499.0 INR 10 444.0 B 171-0030987-7733153 2.3573653923531E13 1.0 499.0 INR 10.1 546.0 B 171-0032103-6712352 2.9477890050147E13 1.0 749.0 INR 10 884.0 B 171-0033662-2427509 3.0127765315035E13 1.0 499.0 INR 10.1 707.0 B 171-0034191-0141945 4.823379397067E12 1.0 499.0 INR 10 1066.0 B 171-0034857-3794740 3.5860646838875E13 2.0 1198.0 INR 10.1 188.0 B 171-0035112-3975520 6.9707840339043E13 1.0 299.0 INR 10 289.0 B 171-0035681-2079506 1.6527618056675E13 1.0 799.0 INR 10.1 1320.0 B 171-0036328-6765939 4.6686953781939E13 1.0 499.0 INR 10 229.0 B 171-0036756-9277149 3.0626920791755E13 1.0 1699.0 INR 10.1 730.0 B 171-0036856-5109160 5.9029121588163E13 1.0 699.0 INR 10 1372.0 B 171-0037142-9207550 2.4699053937387

In [0]:
display(transformed_df)

OrderId OrderItemId QuantityOrdered ItemPrice PromotionDiscount_CurrencyCode PromotionDiscount_Amount batch_id region total_sales net_sale 171-0001135-1657958 1.1168926687715E13 1.0 949.0 INR 10 359.0 A 949.0 939.0 171-0004781-3853173 4.3686103544491E13 1.0 399.0 INR 10.1 809.0 B 399.0 388.9 171-0008662-0057942 6.6326653881907E13 1.0 599.0 INR 10.1 122.0 A 599.0 588.9 171-0010322-1769977 4.7459215833307E13 1.0 399.0 INR 10 676.0 B 399.0 389.0 171-0010803-5365973 2.1135179938611E13 1.0 299.0 INR 10.1 669.0 B 299.0 288.9 171-0015668-5065935 8.918074736283E12 1.0 699.0 INR 10 709.0 A 699.0 689.0 171-0016656-1255573 2.1577356095867E13 1.0 499.0 INR 10.1 695.0 A 499.0 488.9 171-0018345-8874731 5.9365948515931E13 1.0 599.0 INR 10 150.0 A 599.0 589.0 171-0022691-4700335 6.0239001823435E13 1.0 499.0 INR 10 64.0 A 499.0 489.0 171-0023912-2838777 1.2927344177755E13 1.0 499.0 INR 10.1 910.0 A 499.0 488.9 171-0025528-4025152 4.9285731071411E13 1.0 549.0 INR 10.1 872.0 B 549.0 538.9 171-0027470-8653903 2.5200477199443E13 1.0 465.25 INR 10.1 461.0 B 465.25 455.15 171-0028216-8371541 1.0924415207611E13 1.0 1749.0 INR 10 700.0 A 1749.0 1739.0 171-0029459-4938769 1.2269526562963E13 1.0 549.0 INR 10 859.0 A 549.0 539.0 171-0030933-1962721 5.7741977969195E13 1.0 499.0 INR 10 444.0 A 499.0 489.0 171-0030987-7733153 2.3573653923531E13 1.0 499.0 INR 10.1 546.0 A 499.0 488.9 171-0032103-6712352 2.9477890050147E13 1.0 749.0 INR 10 884.0 A 749.0 739.0 171-0032103-6712352 2.9477890050147E13 1.0 749.0 INR 10 884.0 B 749.0 739.0 171-0034191-0141945 4.823379397067E12 1.0 499.0 INR 10 1066.0 B 499.0 489.0 171-0034857-3794740 3.5860646838875E13 2.0 1198.0 INR 10.1 188.0 A 2396.0 2385.9 171-0035112-3975520 6.9707840339043E13 1.0 299.0 INR 10 289.0 B 299.0 289.0 171-0036328-6765939 4.6686953781939E13 1.0 499.0 INR 10 229.0 A 499.0 489.0 171-0036756-9277149 3.0626920791755E13 1.0 1699.0 INR 10.1 730.0 B 1699.0 1688.9 171-0037283-7862727 4.2974188023923E13 1.0 1749.0 INR 10 233.0 B 1749.0 1739.0 171-0038030-5358746 6.6922224095627E13 1.0 499.0 INR 10 958.0 B 499.0 489.0 171-0043140-1568305 3.6514293163019E13 1.0 499.0 INR 10 1464.0 A 499.0 489.0 171-0048393-4049957 6.7270395531563E13 1.0 699.0 INR 10.1 58.0 B 699.0 688.9 171-0051151-8917164 3.7758597660211E13 1.0 799.0 INR 10.1 1053.0 A 799.0 788.9 171-0051434-6217902 6.8437058928619E13 1.0 1999.0 INR 10 26.0 B 1999.0 1989.0 171-0054608-3641930 2.6591641145523E13 1.0 499.0 INR 10 884.0 B 499.0 489.0 171-0060186-9892334 3.6258111172795E13 1.0 649.0 INR 10.1 653.0 A 649.0 638.9 171-0060186-9892334 3.6258111172795E13 1.0 649.0 INR 10.1 653.0 B 649.0 638.9 171-0064902-3332371 3.6686248296035E13 1.0 399.0 INR 10 20.0 A 399.0 389.0 171-0064902-3332371 3.6686248296035E13 1.0 399.0 INR 10 20.0 B 399.0 389.0 171-0065628-5838755 6.1927152671851E13 1.0 399.0 INR 10.1 105.0 A 399.0 388.9 171-0065731-1545177 3.0514886965435E13 1.0 279.0 INR 10 30.0 B 279.0 269.0 171-0066467-2265136 4.9840923889723E13 1.0 539.0 INR 10 1007.0 A 539.0 529.0 171-0066814-8756311 5.2477893499555E13 1.0 699.0 INR 10.1 278.0 B 699.0 688.9 171-0067594-8053912 4.1577518733147E13 1.0 1440.0 INR 10 80.0 A 1440.0 1430.0 171-0067594-8053912 4.1577518733147E13 1.0 1440.0 INR 10 80.0 B 1440.0 1430.0 171-0071045-9666733 2.5207463517995E13 1.0 499.0 INR 10.1 1205.0 A 499.0 488.9 171-0076310-3709148 7.352790206227E12 1.0 699.0 INR 10 46.0 A 699.0 689.0 171-0076310-3709148 7.352790206227E12 1.0 699.0 INR 10 46.0 B 699.0 689.0 171-0079846-8216315 5.9649585575827E13 1.0 1349.0 INR 10.1 87.0 A 1349.0 1338.9 171-0082325-8571521 2.3166092690827E13 1.0 399.0 INR 10.1 300.0 B 399.0 388.9 171-0082628-5593950 4.7892322828899E13 1.0 749.0 INR 10 367.0 B 749.0 739.0 171-0083001-2786714 1.1691134498795E13 1.0 359.0 INR 10 422.0 B 359.0 349.0 171-0084639-5623535 1.4222826971539E13 1.0 1999.0 INR 10 91.0 A 1999.0 1989.0 171-0087005-4381906 6.7895131335219E13 1.0 1999.0 INR 10 286.0 A 1999.0 1989.0 171-0087909-4106719 2.7797814510011E13 1.0 1399.0 INR 10.1 46.0 A 1399.0 1388

Validation

In [0]:
def validate_data(df):
    # Total records
    print(f"Total Records: {df.count()}")
    
    # Sales by region
    df.groupBy("region") \
      .sum("total_sales") \
      .show()
    
    # Average sales
    df.agg({"total_sales": "avg"}) \
      .show()
    
    # Duplicate check
    duplicates = df.groupBy(["OrderId","region"]) \
                   .count() \
                   .filter(col("count") > 1)
    
    if duplicates.count() > 0:
        print("Warning: Duplicate OrderIds found!")
    else:
        print("No duplicates found.")

In [0]:
validate_data(transformed_df)

Total Records: 82104
+------+-------------------+
|region|   sum(total_sales)|
+------+-------------------+
|     B|3.457098452000002E7|
|     A|      3.457098452E7|
+------+-------------------+

+-----------------+
| avg(total_sales)|
+-----------------+
|842.1266812822765|
+-----------------+

No duplicates found.


In [0]:
%sql
-- Count total records
SELECT COUNT(*) as total_records 
FROM sales_data;


total_records 82104

In [0]:
%sql
-- Total sales by region
SELECT region, 
       SUM(total_sales) as total_sales_amount
FROM sales_data
GROUP BY region;


region total_sales_amount B 3.457098452000002E7 A 3.457098452E7

In [0]:
%sql
-- Average sales per transaction
SELECT AVG(total_sales) as avg_sales_per_transaction
FROM sales_data;


avg_sales_per_transaction 842.1266812822765

In [0]:
%sql
-- Check for duplicate OrderIds
SELECT OrderId,region, COUNT(*) as count
FROM sales_data
GROUP BY OrderId,region
HAVING count > 1;

OrderId region count